## Model comparison using traceability analysis
We use the infrastructure built so far to compare two ore more models.
The workhorse will be an iterator (returned by a general function). That allows us to compute and easily access the desired timelines with python index notation it[2:5] will return the values from position 2 to 5 of the solution (and desired variables).
The notebook also contains some functions to compute where the times of two models overlap and some plot functions 

In [1]:
%load_ext autoreload
%autoreload 2
import json
from typing import Tuple
from importlib import import_module
from pathlib import Path
from frozendict import frozendict
import numpy as np
from functools import lru_cache
import bgc_md2.display_helpers as dh
import bgc_md2.helper as h
from bgc_md2.resolve.mvars import (
    CompartmentalMatrix,
    InputTuple,
    StateVariableTuple
)
import general_helpers as gh


# define some shortcut functions that yield the result depending on the 
# model folder  mf
def sim_day_2_day_aD_func(mf): #->function
    return gh.msh(mf).make_sim_day_2_day_since_a_D(gh.confDict(mf))

def tracebility_iterator(mf,delta_t_val):
    ta=gh.test_args(mf)
    mvs_t=gh.mvs(mf)
    dvs_t=ta.dvs
    cpa_t=ta.cpa
    epa_t=ta.epa_0
    X_0=gh.msh(mf).numeric_X_0(mvs_t,dvs_t,cpa_t,epa_t)
    func_dict=gh.msh(mf).make_func_dict(mvs_t,dvs_t,cpa_t,epa_t)
    
    return gh.traceability_iterator(
        X_0,
        func_dict,
        mvs=mvs_t,
        dvs=dvs_t,
        cpa=cpa_t,
        epa=epa_t,
        delta_t_val=delta_t_val
    )
    
model_folders=['yz_jules','kv_visit2']#, 'Aneesh_SDGVM', 'kv_ft_dlem', 'jon_yib']#,'Aneesh_SDGVM','cable-pop','yz_jules']#,]
mf=model_folders[0]

HTML(value='<style>.container { width:100% !important; }</style>')

In [2]:
def times_in_days_aD(mf,delta_t_val):
    n_months=len(gh.test_args(mf).dvs[0])
    n_days=n_months*30
    n_iter=int(n_days/delta_t_val)
    days_after_sim_start=delta_t_val*np.arange(n_iter)
    return np.array(tuple(map(sim_day_2_day_aD_func(mf),days_after_sim_start)))

delta_t_val=30 # assuming the same step size for every model (could be made model specific by an additional testarg)

In [3]:
def t_min_tmax(model_folders,delta_t_val):
    td={
        mf: times_in_days_aD(mf,delta_t_val)
        for mf in model_folders
    }
    t_min = max([t.min() for t in td.values()])
    t_max = min([t.max() for t in td.values()])
    return (t_min,t_max)

t_min_tmax(model_folders,delta_t_val)

reading  cVeg , size is  (3840, 144, 192)
reading  cSoil , size is  (3840, 144, 192)
reading  rh , size is  (3840, 144, 192)
reading  fVegSoil , size is  (3840, 144, 192)
reading  npp_nlim , size is  (3840, 144, 192)
reading  mrsos , size is  (3840, 144, 192)
reading  tsl , size is  (3840, 4, 144, 192)
converted size is  (3840, 144, 192)
reading  landCoverFrac , size is  (3840, 17, 144, 192)
creating a zero arry, shape is  (3840, 144, 192)
{CompartmentalMatrix,InputTuple}
{InFluxesBySymbol,SmoothReservoirModel,CompartmentalMatrix,InputTuple,InternalFluxesBySymbol,OutFluxesBySymbol}
{InFluxesBySymbol,SmoothReservoirModel,CompartmentalMatrix,InputTuple,InternalFluxesBySymbol,OutFluxesBySymbol}
 Found cached global mean files. If you want to recompute the global means
            remove the following files: 
/home/data/VISIT/test/VISIT_S2_cVeg_gm.nc
/home/data/VISIT/test/VISIT_S2_cLitter_gm.nc
/home/data/VISIT/test/VISIT_S2_cSoil_gm.nc
/home/data/VISIT/test/VISIT_S2_rh_gm.nc
/home/data/VI

(679000.0, 735807.5)

In [4]:
#find the timesteps corresponding to shared times
from functools import reduce
def min_max_index(mf,delta_t_val,t_min,t_max):
    ts=times_in_days_aD(mf,delta_t_val)
    def count(acc,i):
        min_i,max_i = acc
        t=ts[i]
        min_i = min_i+1 if t < t_min else min_i 
        max_i = max_i+1 if t < t_max else max_i 
        return (min_i,max_i)
    
    return reduce(count,range(len(ts)),(0,0)) 

s=slice(*min_max_index("yz_jules",delta_t_val,*t_min_tmax(model_folders,delta_t_val)))
s.step is None 

#ind_d={mf: min_max_index(mf) for mf in model_folders}

True

In [17]:
# You can use python index notation on the iterator
# it works the same way as  with a list
l=[1,2,3,4,5,6,7,8,9]
l[3:8:2]

[4, 6, 8]

In [18]:
itr=tracebility_iterator(mf,delta_t_val)
itr[3:8:2] 

TraceTuple(X=array([[[0.65464161],
        [4.22082803],
        [0.65464161],
        [0.04203145],
        [3.28529937],
        [0.28736512],
        [9.52624876]],

       [[0.65795726],
        [4.22399296],
        [0.65795726],
        [0.03527641],
        [3.26974081],
        [0.28690271],
        [9.52654502]],

       [[0.6668182 ],
        [4.23207579],
        [0.6668182 ],
        [0.02852417],
        [3.23739643],
        [0.28574676],
        [9.52618227]]]), X_p=array([[[-0.05853122],
        [-0.32482078],
        [-0.05853122],
        [-0.00443685],
        [ 0.08060815],
        [-0.01042776],
        [ 0.18761734]],

       [[ 0.13171922],
        [ 0.93710689],
        [ 0.13171922],
        [-0.00356372],
        [-0.43045118],
        [-0.05329398],
        [-1.33247577]],

       [[ 0.19910982],
        [ 1.42738237],
        [ 0.19910982],
        [ 0.00323524],
        [-0.39392276],
        [-0.05179378],
        [-1.32003805]]]), X_c=array([[[0.5961104 ]

In [7]:
mf='kv_visit2'
mf="yz_jules"
start,stop=min_max_index(mf,delta_t_val,*t_min_tmax(model_folders,delta_t_val))
start,stop

(1946, 3839)

In [8]:
times=times_in_days_aD(mf,delta_t_val)[start:stop]/365
vals=itr[start:stop]
vals.X_c.shape,times.shape 
#vals

((1893, 7, 1), (1893,))

In [9]:
import matplotlib.pyplot as plt
def plot_sums(model_folders,delta_t_val):
    n = len(model_folders)
    fig=plt.figure(figsize=((n+1)*10,20), dpi = 400)
    axs=fig.subplots(1,n)
    plt.rcParams['font.size'] = 20
    names=['X','X_c','X_p']
    cd={
            'X':"green",
            'X_c':"orange",
            'X_p':"blue"
    }
    for i,mf in enumerate(model_folders):
        itr=tracebility_iterator(mf,delta_t_val)
        start,stop=min_max_index(mf,delta_t_val,*t_min_tmax(model_folders,delta_t_val))
        #tups=values(itr,start,stop)
        #vals=values_2_TraceTuple(tups)
        vals=itr[start:stop]
        times=times_in_days_aD(mf,delta_t_val)[start:stop]/365
        ax=axs[i]
        for name in names:
            ax.plot(
                times,
                vals.__getattribute__(name).sum(axis=1),
                label=name+"_sum",
                color=cd[name]
            )
        ax.legend()
        ax.set_title(mf)
    #plt.close(fig)
    
plot_sums(model_folders,delta_t_val)

## temporal averages
In some cases you might want to see a yearly or monthly average.
You could compute all the values and then compute the averages of parts of the arrays.
The iterator can also do it for you (without storing the unnecessary potentially huge intermediate fine grained arrays).

In [11]:
def partitions(start,stop,nr_acc=1):
    diff=stop-start
    step=nr_acc
    number_of_steps=int(diff/step)
    last_start=start+number_of_steps*step
    last_tup=(last_start,stop)
    return [
        (
            start + step * i,
            start + step *(i+1)
        )
        for i in range(number_of_steps)
    ]+[last_tup]

len(partitions(start,stop,12))

158

In [13]:
itr=tracebility_iterator(mf,delta_t_val)
start,stop=min_max_index(mf,delta_t_val,*t_min_tmax(model_folders,delta_t_val))
tavg_vals=itr.averaged_values(
    partitions(start,stop,12)
)

In [14]:
tavg_vals.X.shape

(158, 7, 1)

In [15]:
def averaged_times(times,partitions):
    return np.array(
        [
            times[p[0]:p[1]].sum()/(p[1]-p[0]) for p in partitions
        ]
    )
    
averaged_times(
    times_in_days_aD(mf,delta_t_val),
    partitions(start,stop,12)
).shape

(158,)

In [19]:
def plot_yearly_avg_sums(model_folders,delta_t_val):
    n = len(model_folders)
    fig=plt.figure(figsize=((n+1)*10,20), dpi = 400)
    axs=fig.subplots(1,n)
    plt.rcParams['font.size'] = 20
    names=['X','X_c','X_p']
    cd={
            'X':"green",
            'X_c':"orange",
            'X_p':"blue"
    }
    for i,mf in enumerate(model_folders):
        itr=tracebility_iterator(mf,delta_t_val)
        start,stop=min_max_index(mf,delta_t_val,*t_min_tmax(model_folders,delta_t_val))
        parts=partitions(start,stop,12)
        times=averaged_times(
            times_in_days_aD(mf,delta_t_val)/365,
            parts
        )
        #vals=averaged_values(
        #    itr,
        #    parts
        #)
        vals=itr.averaged_values(
            parts
        )
        ax=axs[i]
        for name in names:
            ax.plot(
                times,
                vals.__getattribute__(name).sum(axis=1),
                label=name+"_avg_sum",
                color=cd[name]
            )
        ax.legend()
        ax.set_title(mf)
        
plot_yearly_avg_sums(model_folders,delta_t_val)